# IPM geometry optimization

This example shows how to use PyAEDT to find the best machine 2D geometry
to achieve high torque and low losses.
The example shows how to setup an optimetrics analysis to sweep geometries
for a single value of stator current angle.
The torque and losses results are then exported in a .csv file.

Keywords: **Maxwell 2D**, **transient**, **motor**, **optimization**.

## Perform imports and define constants

Perform required imports.

In [1]:
import csv
import os
import tempfile
import time

In [2]:
import ansys.aedt.core

Define constants.

In [3]:
AEDT_VERSION = "2024.2"
NUM_CORES = 4
NG_MODE = False  # Open AEDT UI when it is launched.

## Create temporary directory and download files

Create a temporary directory where downloaded data or
dumped data can be stored.
If you'd like to retrieve the project data for subsequent use,
the temporary folder name is given by ``temp_folder.name``.

In [4]:
temp_folder = tempfile.TemporaryDirectory(suffix=".ansys")

## Download AEDT file example

Set the local temporary folder to export the AEDT file to.

In [5]:
aedt_file = ansys.aedt.core.downloads.download_file(
    source="maxwell_motor_optimization",
    name="IPM_optimization.aedt",
    destination=temp_folder.name,
)

## Launch Maxwell 2D

Launch AEDT and Maxwell 2D after first setting up the project, the version and the graphical mode.

In [6]:
m2d = ansys.aedt.core.Maxwell2d(
    project=aedt_file,
    version=AEDT_VERSION,
    new_desktop=True,
    non_graphical=NG_MODE,
)

PyAEDT INFO: Parsing C:\Users\ansys\AppData\Local\Temp\tmpr_yiop8e.ansys\maxwell_motor_optimization\IPM_optimization.aedt.


PyAEDT INFO: Python version 3.10.11 (tags/v3.10.11:7d4cc5a, Apr  5 2023, 00:38:17) [MSC v.1929 64 bit (AMD64)]


PyAEDT INFO: PyAEDT version 0.12.dev0.


PyAEDT INFO: Initializing new Desktop session.


PyAEDT INFO: Log on console is enabled.


...

PyAEDT INFO: AEDT installation Path C:\Program Files\AnsysEM\v242\Win64


PyAEDT INFO: Ansoft.ElectronicsDesktop.2024.2 version started with process ID 8808.


PyAEDT INFO: Project IPM_optimization has been opened.


PyAEDT INFO: Active Design set to M2D_Transient


PyAEDT INFO: Aedt Objects correctly read


## Add parametric setup

Add a parametric setup made up of geometry variable sweep definitions and single value for the stator current angle.
Note: Step variations have been minimized to reduce the analysis time. If needed they can be increased by changing
the ``step`` argument.

In [7]:
param_sweep = m2d.parametrics.add(
    variable="bridge",
    start_point="0.5mm",
    end_point="1mm",
    step="0.5mm",
    variation_type="LinearStep",
)
param_sweep.add_variation(
    sweep_variable="din",
    start_point=70,
    end_point=80,
    step=10,
    units="mm",
    variation_type="LinearStep",
)
param_sweep.add_variation(
    sweep_variable="phase_advance",
    start_point=0,
    end_point=45,
    step=45,
    units="deg",
    variation_type="LinearStep",
)
param_sweep.add_variation(
    sweep_variable="Ipeak", start_point=200, units="A", variation_type="SingleValue"
)

True

## Analyze parametric sweep

In [8]:
param_sweep.analyze(cores=NUM_CORES)

PyAEDT INFO: Key Desktop/ActiveDSOConfigurations/Maxwell 2D correctly changed.


PyAEDT INFO: Solving Optimetrics


PyAEDT INFO: Key Desktop/ActiveDSOConfigurations/Maxwell 2D correctly changed.


PyAEDT INFO: Design setup Parametric_TXHJCX solved correctly in 0.0h 12.0m 11.0s


True

## Post-processing

Create reports to get torque and loss results for all variations.

In [9]:
report_torque = m2d.post.create_report(
    expressions="Moving1.Torque",
    domain="Sweep",
    variations={"bridge": "All", "din": "All", "Ipeak": "All"},
    primary_sweep_variable="Time",
    plot_type="Rectangular Plot",
    plot_name="TorqueAllVariations",
)

PyAEDT INFO: Modeler2D class has been initialized!


PyAEDT INFO: Modeler class has been initialized! Elapsed time: 0m 0sec


PyAEDT INFO: PostProcessor class has been initialized! Elapsed time: 0m 0sec


PyAEDT INFO: Post class has been initialized! Elapsed time: 0m 0sec


In [10]:
report_solid_loss = m2d.post.create_report(
    expressions="SolidLoss",
    domain="Sweep",
    variations={"bridge": "All", "din": "All", "Ipeak": "All"},
    primary_sweep_variable="Time",
    plot_type="Rectangular Plot",
    plot_name="SolidLossAllVariations",
)

In [11]:
report_core_loss = m2d.post.create_report(
    expressions="CoreLoss",
    domain="Sweep",
    variations={"bridge": "All", "din": "All", "Ipeak": "All"},
    primary_sweep_variable="Time",
    plot_type="Rectangular Plot",
    plot_name="CoreLossAllVariations",
)

Get torque and loss solution data for all available variations.

In [12]:
torque_data = m2d.post.get_solution_data(
    expressions=["Moving1.Torque"],
    setup_sweep_name=m2d.nominal_sweep,
    domain="Sweep",
    variations={"bridge": "All", "din": "All", "Ipeak": "All"},
    primary_sweep_variable="Time",
    report_category="Standard",
)

PyAEDT INFO: Solution Data Correctly Loaded.


In [13]:
solid_loss_data = m2d.post.get_solution_data(
    expressions=["CoreLoss"],
    setup_sweep_name=m2d.nominal_sweep,
    domain="Sweep",
    variations={"bridge": "All", "din": "All", "Ipeak": "All"},
    primary_sweep_variable="Time",
    report_category="Standard",
)

PyAEDT INFO: Solution Data Correctly Loaded.


In [14]:
core_loss_data = m2d.post.get_solution_data(
    expressions=["SolidLoss"],
    setup_sweep_name=m2d.nominal_sweep,
    domain="Sweep",
    variations={"bridge": "All", "din": "All", "Ipeak": "All"},
    primary_sweep_variable="Time",
    report_category="Standard",
)

PyAEDT INFO: Solution Data Correctly Loaded.


Calculate torque and loss average values for each variation and write data in a .csv file.

In [15]:
csv_data = []
for var in core_loss_data.variations:
    torque_data.active_variation = var
    core_loss_data.active_variation = var
    solid_loss_data.active_variation = var

    torque_values = torque_data.data_magnitude()
    core_loss_values = core_loss_data.data_magnitude()
    solid_loss_values = solid_loss_data.data_magnitude()

    torque_data_average = sum(torque_values) / len(torque_values)
    core_loss_average = sum(core_loss_values) / len(core_loss_values)
    solid_loss_average = sum(solid_loss_values) / len(solid_loss_values)

    csv_data.append(
        {
            "active_variation": str(torque_data.active_variation),
            "average_torque": str(torque_data_average),
            "average_core_loss": str(core_loss_average),
            "average_solid_loss": str(solid_loss_average),
        }
    )

    with open(
        os.path.join(temp_folder.name, "motor_optimization.csv"), "w", newline=""
    ) as csvfile:
        fields = [
            "active_variation",
            "average_torque",
            "average_core_loss",
            "average_solid_loss",
        ]
        writer = csv.DictWriter(csvfile, fieldnames=fields)
        writer.writeheader()
        writer.writerows(csv_data)

## Release AEDT

In [16]:
m2d.save_project()
m2d.release_desktop()
# Wait 3 seconds to allow AEDT to shut down before cleaning the temporary directory.
time.sleep(3)

PyAEDT INFO: Project IPM_optimization Saved correctly


PyAEDT INFO: Desktop has been released and closed.


## Clean up

All project files are saved in the folder ``temp_folder.name``.
If you've run this example as a Jupyter notebook, you
can retrieve those project files. The following cell
removes all temporary files, including the project folder.

In [17]:
temp_folder.cleanup()